In [16]:
#import lightgbm
import random
import pandas as pd
import numpy as np
import os
from xgboost import XGBRegressor
from sklearn.ensemble import RandomForestRegressor
import matplotlib.pyplot as plt
from tqdm import tqdm
from sklearn.model_selection import PredefinedSplit, GridSearchCV
from sktime.forecasting.model_selection import temporal_train_test_split
from sktime.utils.plotting import plot_series
from xgboost import XGBRegressor
import time
from sklearn.metrics import make_scorer
t = time.strftime('%m%d-%H%M', time.localtime(time.time()))
import warnings
warnings.filterwarnings(action='ignore')

def seed_everything(seed):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)

seed_everything(42) # Seed 고정
#### alpha를 argument로 받는 함수로 실제 objective function을 wrapping하여 alpha값을 쉽게 조정할 수 있도록 작성했습니다.
# custom objective function for forcing model not to underestimate
def weighted_mse(alpha = 1):
    def weighted_mse_fixed(label, pred):
        residual = (label - pred).astype("float")
        grad = np.where(residual>0, -2*alpha*residual, -2*residual)
        hess = np.where(residual>0, 2*alpha, 2.0)
        return grad, hess
    return weighted_mse_fixed

 #점수 측정을 위한 코드
def SMAPE(y_true, y_pred):
    return 100/len(y_true) * np.sum(2 * np.abs(y_pred - y_true) / (np.abs(y_true) + np.abs(y_pred)))

깊이 튜닝

In [17]:
hyperparameters = pd.DataFrame(columns = ['n_estimators', 'eta', 'min_child_weight','max_depth', 'colsample_bytree', 'subsample'])
preds = np.array([])

grid = {'n_estimators' : [100], 'eta' : [0.01], 'min_child_weight' : np.arange(1, 12, 1),
        'max_depth' : np.arange(3,10,1) , 'colsample_bytree' :[0.8, 0.9],
        'subsample' : [0.8, 0.9]} # fix the n_estimators & eta(learning rate)

#tscv = TimeSeriesSplit(n_splits=3)
smape_score = make_scorer(SMAPE, greater_is_better=False)

for i in tqdm(np.arange(1, 101, 1)):
    train_df = pd.read_csv(f'./split/train_valid_building{i}.csv').drop(columns='Unnamed: 0')
    valid_df = pd.read_csv(f'./split/valid_building{i}.csv').drop(columns='Unnamed: 0')
    pretest_df = pd.read_csv(f'./split/pretest_building{i}.csv').drop(columns='Unnamed: 0')
    merge = pd.concat([train_df,valid_df])


    pretest_y = pretest_df['power_consumption']
    pretest_x = pretest_df.drop(columns=['power_consumption'])
    #하이퍼 파라미터 튜닝 method 1
    #leaf method
    print(f"__________Buildding Number:{i} Hyperparameter Tuning__________")

    preds = np.array([])
    smape_score = make_scorer(SMAPE, greater_is_better=False)
    grid = {'n_estimators' : [100], 'eta' : [0.01], 'min_child_weight' : np.arange(1, 12, 1), 'max_depth' : np.arange(3,10,1) , 'colsample_bytree' :[0.8, 0.9], 'subsample' : [0.8, 0.9]} 
    grid_under = {}
    #합병된 데이터 사용
    y = merge['power_consumption']
    x = merge.drop(columns=['power_consumption'])
    y_train, y_test, x_train, x_test = temporal_train_test_split(y = y, X = x, test_size = 168)
    #fit
    gcv = GridSearchCV(estimator = XGBRegressor(seed=42,tree_method="hist", gpu_id=0), param_grid=grid, scoring=smape_score, cv=PredefinedSplit(np.append(-np.ones(len(x)-168), np.zeros(168))) ,refit=True, verbose=False)
    gcv.fit(x, y)

    best = gcv.best_estimator_
    params = gcv.best_params_

    #pred
    x_pretest = pretest_df.drop(columns=['power_consumption'])
    y_pretest = pretest_df['power_consumption']
    pred = best.predict(x_pretest)
    print("_____Best Parameters_____",params)
    print("_____SMAPE Score________", SMAPE(y_pretest, pred))
    hyperparameters = pd.concat([hyperparameters,pd.DataFrame(params,index=[i-1])],axis=0)
hyperparameters.to_csv(f'./parameters/hyperparameter_xgb_wsw{t}.csv', index=False) # save the tuned parameters


  0%|          | 0/100 [00:00<?, ?it/s]

__________Buildding Number:1 Hyperparameter Tuning__________


  0%|          | 0/100 [00:05<?, ?it/s]


KeyboardInterrupt: 

n_estimators 튜닝

In [12]:
#n_estimators
xgb_params = pd.read_csv(f'./parameters/hyperparameter_xgb_wsw{t}.csv')
scores = []   # smape 값을 저장할 list
best_it = []  # best interation을 저장할 list
for i in tqdm(range(100)):
    train_df = pd.read_csv(f'./split/train_valid_building{i+1}.csv').drop(columns='Unnamed: 0')
    valid_df = pd.read_csv(f'./split/valid_building{i+1}.csv').drop(columns='Unnamed: 0')
    pretest_df = pd.read_csv(f'./split/pretest_building{i+1}.csv').drop(columns='Unnamed: 0')
    y = train_df['power_consumption']
    x = train_df.drop(['power_consumption'], axis=1)
    v_y = valid_df['power_consumption']
    v_x = valid_df.drop(['power_consumption'], axis=1)
    p_y = pretest_df['power_consumption']
    p_x = pretest_df.drop(['power_consumption'], axis=1)

    xgb_reg = XGBRegressor(n_estimators = 10000, tree_method="hist",  gpu_id=0, 
                           eta = 0.01, 
                           min_child_weight = xgb_params.iloc[i, 2],
                           max_depth = xgb_params.iloc[i, 3], 
                           colsample_bytree = xgb_params.iloc[i, 4],
                           subsample = xgb_params.iloc[i, 5], 
                           seed=0)
    xgb_reg.set_params(**{'objective':weighted_mse(100)}) # alpha = 100으로 고정

    xgb_reg.fit(x_train, y_train, eval_set=[(x, y),
                                            (v_x, v_y)], early_stopping_rounds=300, verbose=False)
    y_pred = xgb_reg.predict(p_x)
    pred = pd.Series(y_pred)

    sm = SMAPE(p_y, y_pred)
    scores.append(sm)
    best_it.append(xgb_reg.best_iteration+1) ## 실제 best iteration은 이 값에 +1 해주어야 함.
hyperparameters['best_it'] = best_it

100%|██████████| 100/100 [02:30<00:00,  1.50s/it]


alpha튜닝

In [13]:

#alpha
alpha_list = []
smape_list = []
for i in tqdm(range(100)):
    train_df = pd.read_csv(f'./split/train_valid_building{i+1}.csv').drop(columns='Unnamed: 0')
    valid_df = pd.read_csv(f'./split/valid_building{i+1}.csv').drop(columns='Unnamed: 0')
    pretest_df = pd.read_csv(f'./split/pretest_building{i+1}.csv').drop(columns='Unnamed: 0')
    
    y = train_df['power_consumption']
    x = train_df.drop(['power_consumption'], axis=1)
    v_y = valid_df['power_consumption']
    v_x = valid_df.drop(['power_consumption'], axis=1)
    p_y = pretest_df['power_consumption']
    p_x = pretest_df.drop(['power_consumption'], axis=1)

    xgb = XGBRegressor(seed = 0, tree_method="hist",  gpu_id=0,
                      n_estimators = best_it[i], 
                      eta = 0.01, 
                      min_child_weight = xgb_params.iloc[i, 2],
                      max_depth = xgb_params.iloc[i, 3], 
                      colsample_bytree = xgb_params.iloc[i, 4], 
                      subsample = xgb_params.iloc[i, 5])

    xgb.fit(x, y,eval_set=[(x, y),(v_x, v_y)])
    pred0 = xgb.predict(p_x)
    best_alpha = 0
    score0 = SMAPE(p_y,pred0)

    for j in [1, 3, 5, 7, 10, 25, 50, 75, 100]:
        xgb = XGBRegressor(seed = 0,
                      n_estimators = best_it[i], eta = 0.01, min_child_weight = xgb_params.iloc[i, 2],
                      max_depth = xgb_params.iloc[i, 3], colsample_bytree = xgb_params.iloc[i, 4], subsample = xgb_params.iloc[i, 5])
        xgb.set_params(**{'objective' : weighted_mse(j)})

        xgb.fit(x, y)
        pred1 = xgb.predict(p_x)
        score1 = SMAPE(p_y, pred1)
        if score1 < score0:
            best_alpha = j
            score0 = score1

    alpha_list.append(best_alpha)
    smape_list.append(score0)
    print("building {} || best score : {} || alpha : {}".format(i+1, score0, best_alpha))
hyperparameters['alpha'] = alpha_list

  0%|          | 0/100 [00:00<?, ?it/s]

[0]	validation_0-rmse:2816.39745	validation_1-rmse:3008.68649
[1]	validation_0-rmse:2788.73492	validation_1-rmse:2987.00494
[2]	validation_0-rmse:2761.50415	validation_1-rmse:2957.59274
[3]	validation_0-rmse:2734.39349	validation_1-rmse:2936.33136
[4]	validation_0-rmse:2707.53887	validation_1-rmse:2915.27114
[5]	validation_0-rmse:2680.90401	validation_1-rmse:2894.39799
[6]	validation_0-rmse:2654.59894	validation_1-rmse:2873.75702
[7]	validation_0-rmse:2628.50813	validation_1-rmse:2853.21266
[8]	validation_0-rmse:2602.78167	validation_1-rmse:2833.06551
[9]	validation_0-rmse:2577.25414	validation_1-rmse:2813.10484
[10]	validation_0-rmse:2552.12905	validation_1-rmse:2793.31640
[11]	validation_0-rmse:2527.10136	validation_1-rmse:2773.50109
[12]	validation_0-rmse:2502.28194	validation_1-rmse:2753.92955
[13]	validation_0-rmse:2477.78981	validation_1-rmse:2734.51539
[14]	validation_0-rmse:2453.49450	validation_1-rmse:2715.53208
[15]	validation_0-rmse:2429.51943	validation_1-rmse:2696.70583
[1

  1%|          | 1/100 [00:07<11:55,  7.23s/it]

building 1 || best score : 14.306826389204941 || alpha : 100
[0]	validation_0-rmse:1746.32791	validation_1-rmse:1963.53769
[1]	validation_0-rmse:1729.21497	validation_1-rmse:1949.77520
[2]	validation_0-rmse:1712.45095	validation_1-rmse:1931.73046
[3]	validation_0-rmse:1695.69409	validation_1-rmse:1918.05877
[4]	validation_0-rmse:1679.13385	validation_1-rmse:1904.79135
[5]	validation_0-rmse:1662.70645	validation_1-rmse:1891.34750
[6]	validation_0-rmse:1646.46257	validation_1-rmse:1878.10787
[7]	validation_0-rmse:1630.31937	validation_1-rmse:1864.75046
[8]	validation_0-rmse:1614.45339	validation_1-rmse:1851.54064
[9]	validation_0-rmse:1598.66714	validation_1-rmse:1838.51892
[10]	validation_0-rmse:1583.10446	validation_1-rmse:1825.54636
[11]	validation_0-rmse:1567.56826	validation_1-rmse:1812.66200
[12]	validation_0-rmse:1552.32421	validation_1-rmse:1800.24951
[13]	validation_0-rmse:1537.13859	validation_1-rmse:1787.73728
[14]	validation_0-rmse:1522.16489	validation_1-rmse:1775.61873
[15]

  2%|▏         | 2/100 [00:17<14:30,  8.88s/it]

...

building 98 || best score : 13.17468263146888 || alpha : 1
[0]	validation_0-rmse:1197.07221	validation_1-rmse:1298.05520
[1]	validation_0-rmse:1185.25734	validation_1-rmse:1287.97142
[2]	validation_0-rmse:1173.56926	validation_1-rmse:1275.63628
[3]	validation_0-rmse:1161.98687	validation_1-rmse:1265.71838
[4]	validation_0-rmse:1150.51270	validation_1-rmse:1255.45848
[5]	validation_0-rmse:1139.15360	validation_1-rmse:1245.95232
[6]	validation_0-rmse:1127.91527	validation_1-rmse:1236.41865
[7]	validation_0-rmse:1116.78151	validation_1-rmse:1226.43747
[8]	validation_0-rmse:1105.76509	validation_1-rmse:1216.59199
[9]	validation_0-rmse:1094.86766	validation_1-rmse:1207.45274
[10]	validation_0-rmse:1084.05714	validation_1-rmse:1198.74354
[11]	validation_0-rmse:1073.37273	validation_1-rmse:1189.61172
[12]	validation_0-rmse:1062.78091	validation_1-rmse:1180.72355
[13]	validation_0-rmse:1052.28999	validation_1-rmse:1171.78001
[14]	validation_0-rmse:1041.93075	validation_1-rmse:1163.08291
[15]	v

 99%|█████████▉| 99/100 [13:06<00:08,  8.42s/it]

building 99 || best score : 5.572451128256828 || alpha : 100
[0]	validation_0-rmse:863.03677	validation_1-rmse:926.43012
[1]	validation_0-rmse:854.52338	validation_1-rmse:919.24996
[2]	validation_0-rmse:846.10934	validation_1-rmse:910.49527
[3]	validation_0-rmse:837.77381	validation_1-rmse:902.33029
[4]	validation_0-rmse:829.53626	validation_1-rmse:894.29006
[5]	validation_0-rmse:821.37670	validation_1-rmse:886.16436
[6]	validation_0-rmse:813.32372	validation_1-rmse:878.14173
[7]	validation_0-rmse:805.33610	validation_1-rmse:870.31189
[8]	validation_0-rmse:797.42208	validation_1-rmse:862.56967
[9]	validation_0-rmse:789.59768	validation_1-rmse:854.77253
[10]	validation_0-rmse:781.84105	validation_1-rmse:846.85381
[11]	validation_0-rmse:774.16344	validation_1-rmse:839.17889
[12]	validation_0-rmse:766.56311	validation_1-rmse:831.60333
[13]	validation_0-rmse:759.03193	validation_1-rmse:824.20242
[14]	validation_0-rmse:751.57575	validation_1-rmse:817.99524
[15]	validation_0-rmse:744.18600	v

100%|██████████| 100/100 [13:15<00:00,  7.95s/it]

building 100 || best score : 7.2502055212825 || alpha : 100


In [15]:
hyperparameters.to_csv(f'./parameters/hyperparameter_xgb_wsw{t}.csv')